In [5]:
!nvidia-smi

Wed Dec 11 15:28:03 2024       
+-----------------------------------------------------------------------------+
| NVIDIA-SMI 525.116.04   Driver Version: 525.116.04   CUDA Version: 12.0     |
|-------------------------------+----------------------+----------------------+
| GPU  Name        Persistence-M| Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp  Perf  Pwr:Usage/Cap|         Memory-Usage | GPU-Util  Compute M. |
|                               |                      |               MIG M. |
|===============================+======================+======================|
|   0  NVIDIA GeForce ...  On   | 00000000:3D:00.0 Off |                  N/A |
| 27%   28C    P8    10W / 250W |      3MiB / 11264MiB |      0%      Default |
|                               |                      |                  N/A |
+-------------------------------+----------------------+----------------------+
                                                                               
+-------

In [ ]:
# ROOT_DIR = "/data/Multi-GraspLLM"
# import os
# import sys
# sys.path.append(ROOT_DIR)
# os.chdir(ROOT_DIR)

from utils.hand_model import HandModel
from utils.panda_gripper import PandaGripper
import json


urdf_allegro_path="./hand_model/allegro_hand_description/allegro_hand_description_right.urdf"
meshes_allegro_path="./hand_model/allegro_hand_description/meshes"
allegro_hand_model = HandModel("allegro", urdf_allegro_path, meshes_allegro_path, batch_size=1, device="cuda", hand_scale=1)

urdf_shadow_path="./hand_model/shadow_hand_description/urdf/shadowhand_adjust.urdf"
meshes_shadow_path="./hand_model/shadow_hand_description/meshes"
shadow_hand_model = HandModel("shadowhand", urdf_shadow_path, meshes_shadow_path, batch_size=1, device="cuda", hand_scale=1)


panda_gripper=PandaGripper()




only got 88/128 samples!
only got 117/128 samples!
only got 120/128 samples!
only got 119/128 samples!
only got 126/128 samples!
only got 124/128 samples!
only got 120/128 samples!
only got 116/128 samples!
only got 120/128 samples!
only got 121/128 samples!
only got 124/128 samples!


Processing link #0: base_link
Processing link #1: link_0.0
Processing link #2: link_1.0
Processing link #3: link_2.0
Processing link #4: link_3.0
Processing link #5: link_3.0_tip
Processing link #6: link_4.0
Processing link #7: link_5.0
Processing link #8: link_6.0
Processing link #9: link_7.0
Processing link #10: link_7.0_tip
Processing link #11: link_8.0
Processing link #12: link_9.0
Processing link #13: link_10.0
Processing link #14: link_11.0
Processing link #15: link_11.0_tip
Processing link #16: link_12.0
Processing link #17: link_13.0
Processing link #18: link_14.0
Processing link #19: link_15.0
Processing link #20: link_15.0_tip


only got 58/64 samples!
only got 59/64 samples!
only got 63/64 samples!
only got 62/64 samples!
only got 63/64 samples!
only got 62/64 samples!


Processing link #0: palm
Processing link #1: ffknuckle
Processing link #2: ffproximal
Processing link #3: ffmiddle
Processing link #4: ffdistal
Processing link #5: fftip
Processing link #6: mfknuckle
Processing link #7: mfproximal
Processing link #8: mfmiddle
Processing link #9: mfdistal
Processing link #10: mftip
Processing link #11: rfknuckle
Processing link #12: rfproximal
Processing link #13: rfmiddle
Processing link #14: rfdistal
Processing link #15: rftip
Processing link #16: lfmetacarpal
Processing link #17: lfknuckle
Processing link #18: lfproximal


only got 62/64 samples!


Processing link #19: lfmiddle
Processing link #20: lfdistal
Processing link #21: lftip
Processing link #22: thbase
Processing link #23: thproximal
Processing link #24: thhub
Processing link #25: thmiddle
Processing link #26: thdistal
Processing link #27: thtip


In [ ]:
import pickle

with open("./mid-level-data/shadow.pkl","rb") as f:
    meta_shadow=pickle.load(f)

with open("./mid-level-data/allegro.pkl","rb") as f:
    meta_allegro=pickle.load(f)
    
with open("./mid-level-data/panda.pkl","rb") as f:
    meta_panda=pickle.load(f)

# Visualize Allegro Hand

In [ ]:
import trimesh
import re
import torch
import numpy as np
vocab_size=511
object_code="cylinder_bottle_s104"
num=1
angle=meta_allegro[object_code][num]['angle']
obj_id=object_code


infer_pose=torch.tensor(angle[0]+angle[1][:, :2].T.ravel().tolist()+angle[2])
mesh_hand_list_infer=allegro_hand_model.get_meshes_from_q(q=infer_pose.cuda().unsqueeze(0))
mesh_hand= trimesh.util.concatenate(mesh_hand_list_infer)

pc=np.load(f"./pc_8192/{obj_id}.npy")[:,:3]
point_colors = np.tile([255, 0, 0, 255], (pc.shape[0], 1))
point_cloud = trimesh.points.PointCloud(pc,colors=point_colors)
print(meta_allegro[object_code][num]['contact_info'])
scene = trimesh.Scene()
scene.add_geometry(point_cloud)
scene.add_geometry(mesh_hand)
scene.show()

['Little finger,middle finger,thumb finger and index finger touch the bottle body of cylinder_bottle.', 'Little finger,middle finger,thumb finger and index finger touch the bottle body of cylinder_bottle.']


# Visualize Shadow Hand

In [16]:
import trimesh
import re
vocab_size=511
object_code="mug_s139"
num=1
angle=meta_shadow[object_code][num]['angle']
obj_id=object_code





infer_pose=torch.tensor(angle[0]+angle[1][:, :2].T.ravel().tolist()+angle[2])
mesh_hand_list_infer=shadow_hand_model.get_meshes_from_q(q=infer_pose.cuda().unsqueeze(0))
mesh_hand= trimesh.util.concatenate(mesh_hand_list_infer)

print(meta_shadow[object_code][num]['contact_info'])
pc=np.load(f"./data/pc_8192/{obj_id}.npy")[:,:3]
point_colors = np.tile([255, 0, 0, 255], (pc.shape[0], 1))
point_cloud = trimesh.points.PointCloud(pc,colors=point_colors)
scene = trimesh.Scene()
scene.add_geometry(point_cloud)
scene.add_geometry(mesh_hand)
scene.show()

['Little finger,ring finger,middle finger,thumb finger and index finger touch the mug body of mug.', 'all fingers touches the mug body of mug']


# Visual Panda Gripper

In [20]:
object_code="chaoneng_handwash"
print(meta_panda[object_code].keys())

angle=meta_panda[object_code]['pump head'][0]
mesh_hand=panda_gripper.get_meshes(angle)

pc=np.load(f"./data/pc_8192/{object_code}.npy")[:,:3]
point_colors = np.tile([255, 0, 0, 255], (pc.shape[0], 1))
point_cloud = trimesh.points.PointCloud(pc,colors=point_colors)
scene = trimesh.Scene()
scene.add_geometry(point_cloud)
scene.add_geometry(mesh_hand)
scene.show()

dict_keys(['pump head', 'bottle body'])
